In [0]:
import os

client_id = os.environ.get('client_id')
tenant_id = os.environ.get('tenant_id')
client_secret = os.environ.get('secret_value')
storage_account = "project1azure1"

spark.conf.set(f"fs.azure.account.auth.type.{storage_account}.dfs.core.windows.net", "OAuth")
spark.conf.set(f"fs.azure.account.oauth.provider.type.{storage_account}.dfs.core.windows.net", "org.apache.hadoop.fs.azurebfs.oauth2.ClientCredsTokenProvider")
spark.conf.set(f"fs.azure.account.oauth2.client.id.{storage_account}.dfs.core.windows.net", client_id)
spark.conf.set(f"fs.azure.account.oauth2.client.secret.{storage_account}.dfs.core.windows.net", client_secret)
spark.conf.set(f"fs.azure.account.oauth2.client.endpoint.{storage_account}.dfs.core.windows.net", f"https://login.microsoftonline.com/{tenant_id}/oauth2/token")

Reading Data from adls

In [0]:
df_event = spark.read.format("delta").load("abfss://silver@project1azure1.dfs.core.windows.net/sales/events", header=True)
df_item_properties = spark.read.format("delta").load("abfss://silver@project1azure1.dfs.core.windows.net/inventory/item_properties", header=True)

In [0]:
from pyspark.sql.functions import col, when, count, lit, max, round 
from pyspark.sql.types import IntegerType

category_df = df_item_properties.filter(col("property") == "categoryid")


#Current category column
latest_category_df = category_df.groupBy("itemid").agg(max(col("timestamp")).alias("latest_timestamp")).join(category_df, "itemid").filter(col("timestamp") == col("latest_timestamp")).select("itemid", "value").withColumnRenamed("value", "current_category_id")


availabilty_df = df_item_properties.filter(col("property") == "available")

#Current availaibilty column
latest_availability_df = availabilty_df.groupBy("itemid").agg(max(col("timestamp")).alias("latest_timestamp")).join(availabilty_df, "itemid").filter(col("timestamp") == col("latest_timestamp")).select("itemid", "value").withColumnRenamed("value", "current_availability")


#Total views,Total addtocart and total transaction columns
event_counts = df_event.groupby("itemid", "event").agg(count("*").alias("count"))

pivot_df = event_counts.groupby("itemid").pivot("event",["view","addtocart","transaction"]).sum("count").na.fill(0).withColumnRenamed("view", "total_views").withColumnRenamed("addtocart", "total_addtocarts").withColumnRenamed("transaction", "total_purchases")

dim_item = pivot_df.join(latest_category_df, "itemid","left").join(latest_availability_df, "itemid","left")

#Conversion rate column
dim_item = dim_item.withColumn("Conversion_rate",when(col("total_views") == 0,lit(0.0)).otherwise(round(col("total_purchases")/col("total_views"),4)))

#latest timestamp column
latest_update = df_item_properties.groupBy("itemid").agg(max(col("timestamp")).alias("latest_timestamp"))
dim_item = dim_item.join(latest_update, "itemid","left")

display(dim_item)








itemid total_views total_addtocarts total_purchases current_category_id current_availability Conversion_rate latest_timestamp 91 3 0 0 209 0 0.0 2015-05-31T03:00:00Z 128 4 0 0 null null 0.0 null 193 2 0 0 1528 0 0.0 2015-09-13T03:00:00Z 210 1 0 0 421 0 0.0 2015-05-31T03:00:00Z 251 5 0 0 342 0 0.0 2015-06-28T03:00:00Z 375 8 0 0 1173 0 0.0 2015-05-10T03:00:00Z 412 21 0 0 1018 1 0.0 2015-09-13T03:00:00Z 417 10 0 0 null null 0.0 null 481 13 0 0 1192 0 0.0 2015-05-31T03:00:00Z 496 124 5 2 707 0 0.0161 2015-09-13T03:00:00Z 516 8 0 0 null null 0.0 null 587 1 0 0 1142 0 0.0 2015-06-28T03:00:00Z 667 1 0 0 1634 0 0.0 2015-06-28T03:00:00Z 673 1 0 0 null null 0.0 null 683 4 0 0 1244 0 0.0 2015-09-13T03:00:00Z 731 1 0 0 342 0 0.0 2015-06-28T03:00:00Z 737 2 0 0 624 0 0.0 2015-09-13T03:00:00Z 756 3 0 0 null null 0.0 null 787 2 0 0 null null 0.0 null 860 58 0 0 199 0 0.0 2015-05-31T03:00:00Z 875 14 0 0 1638 0 0.0 2015-06-28T03:00:00Z 988 11 0 0 50 0 0.0 2015-09-13T03:00:00Z 1068 5 0 0 1135 0 0.0 2015-05-31T03:00:00Z 1077 2 0 0 1404 0 0.0 2015-09-13T03:00:00Z 1260 8 0 0 799 0 0.0 2015-06-28T03:00:00Z 1270 1 0 0 1605 0 0.0 2015-06-28T03:00:00Z 1342 4 1 0 126 1 0.0 2015-05-10T03:00:00Z 1352 1 0 0 1474 0 0.0 2015-05-24T03:00:00Z 1398 11 0 0 1203 0 0.0 2015-06-07T03:00:00Z 1415 25 0 0 911 0 0.0 2015-09-13T03:00:00Z 1417 1 0 0 null null 0.0 null 1496 5 0 0 1529 1 0.0 2015-08-16T03:00:00Z 1561 1 0 0 null null 0.0 null 1653 7 2 1 208 1 0.1429 2015-05-31T03:00:00Z 1689 12 0 0 1233 0 0.0 2015-06-07T03:00:00Z 1721 1 0 0 1680 1 0.0 2015-09-13T03:00:00Z 1777 1 0 0 769 0 0.0 2015-09-13T03:00:00Z 1826 2 0 0 1250 0 0.0 2015-06-07T03:00:00Z 1848 2 0 0 1483 0 0.0 2015-05-31T03:00:00Z 1892 13 0 0 528 1 0.0 2015-09-13T03:00:00Z 1896 13 0 0 1233 0 0.0 2015-05-10T03:00:00Z 1977 21 0 0 1248 0 0.0 2015-09-13T03:00:00Z 2003 1 0 0 null null 0.0 null 2006 28 2 0 558 1 0.0 2015-09-13T03:00:00Z 2044 2 0 0 null null 0.0 null 2090 5 0 0 null null 0.0 null 2113 4 0 0 1663 0 0.0 2015-09-13T03:00:00Z 2142 52 7 1 1135 1 0.0192 2015-05-17T03:00:00Z 2169 1 0 0 1390 0 0.0 2015-05-10T03:00:00Z 2288 32 0 0 333 0 0.0 2015-06-28T03:00:00Z 2294 7 0 0 1172 0 0.0 2015-05-24T03:00:00Z 2322 2 0 0 1317 0 0.0 2015-05-10T03:00:00Z 2355 1 0 0 769 0 0.0 2015-06-28T03:00:00Z 2396 12 0 0 274 1 0.0 2015-09-13T03:00:00Z 2502 1 0 0 133 0 0.0 2015-09-13T03:00:00Z 2521 41 0 0 1282 0 0.0 2015-09-13T03:00:00Z 2610 16 0 0 256 1 0.0 2015-09-13T03:00:00Z 2675 2 0 0 1301 0 0.0 2015-05-31T03:00:00Z 2684 1 0 0 null null 0.0 null 2711 100 7 1 411 1 0.01 2015-05-31T03:00:00Z 2738 1 0 0 449 1 0.0 2015-09-13T03:00:00Z 2748 13 0 0 491 0 0.0 2015-09-13T03:00:00Z 2752 1 0 0 null null 0.0 null 2833 4 0 0 1085 0 0.0 2015-09-13T03:00:00Z 2835 2 0 0 null null 0.0 null 2842 1 0 0 421 0 0.0 2015-06-28T03:00:00Z 2920 2 1 0 936 1 0.0 2015-05-10T03:00:00Z 2924 2 0 0 691 0 0.0 2015-05-31T03:00:00Z 2961 10 2 0 739 0 0.0 2015-09-13T03:00:00Z 2971 7 0 0 730 0 0.0 2015-09-13T03:00:00Z 3042 27 0 0 1051 0 0.0 2015-06-28T03:00:00Z 3069 7 0 0 null null 0.0 null 3149 1 0 0 1114 0 0.0 2015-09-13T03:00:00Z 3207 1 0 0 null null 0.0 null 3213 2 0 0 1172 0 0.0 2015-06-28T03:00:00Z 3216 2 0 0 984 0 0.0 2015-05-31T03:00:00Z 3228 1 0 0 683 0 0.0 2015-06-28T03:00:00Z 3264 7 0 0 996 0 0.0 2015-06-28T03:00:00Z 3306 2 0 0 64 0 0.0 2015-05-24T03:00:00Z 3328 2 0 0 null null 0.0 null 3359 1 0 0 984 0 0.0 2015-05-10T03:00:00Z 3441 4 0 0 828 0 0.0 2015-05-31T03:00:00Z 3450 13 0 0 1098 0 0.0 2015-06-28T03:00:00Z 3488 1 0 0 1210 0 0.0 2015-05-31T03:00:00Z 3595 2 0 0 1533 0 0.0 2015-09-13T03:00:00Z 3611 15 0 0 508 0 0.0 2015-05-10T03:00:00Z 3621 1 0 0 799 0 0.0 2015-06-28T03:00:00Z 3650 3 0 0 1172 0 0.0 2015-05-24T03:00:00Z 3725 12 0 0 243 0 0.0 2015-06-28T03:00:00Z 3727 9 1 0 1221 1 0.0 2015-05-10T03:00:00Z 3749 1 0 0 1578 0 0.0 2015-05-31T03:00:00Z 3792 2 0 0 619 0 0.0 2015-09-13T03:00:00Z 3814 4 0 0 618 1 0.0 2015-05-10T03:00:00Z 3834 1 0 0 173 0 0.0 2015-06-28T03:00:00Z 3886 2 0 0 828 0 0.0 2015-05-31T03:00:00Z 3905 2 0 0 598 0 0.0 2015-06-28T03:00:

Converting long type to integer type

In [0]:
cols_to_convert = ["total_views", "total_addtocarts", "total_purchases"]

for column_name in cols_to_convert:
    dim_item = dim_item.withColumn(column_name, col(column_name).cast(IntegerType()))

dim_item.display()

itemid total_views total_addtocarts total_purchases current_category_id current_availability Conversion_rate latest_timestamp 91 3 0 0 209 0 0.0 2015-05-31T03:00:00Z 128 4 0 0 null null 0.0 null 193 2 0 0 1528 0 0.0 2015-09-13T03:00:00Z 210 1 0 0 421 0 0.0 2015-05-31T03:00:00Z 251 5 0 0 342 0 0.0 2015-06-28T03:00:00Z 375 8 0 0 1173 0 0.0 2015-05-10T03:00:00Z 412 21 0 0 1018 1 0.0 2015-09-13T03:00:00Z 417 10 0 0 null null 0.0 null 481 13 0 0 1192 0 0.0 2015-05-31T03:00:00Z 496 124 5 2 707 0 0.0161 2015-09-13T03:00:00Z 516 8 0 0 null null 0.0 null 587 1 0 0 1142 0 0.0 2015-06-28T03:00:00Z 667 1 0 0 1634 0 0.0 2015-06-28T03:00:00Z 673 1 0 0 null null 0.0 null 683 4 0 0 1244 0 0.0 2015-09-13T03:00:00Z 731 1 0 0 342 0 0.0 2015-06-28T03:00:00Z 737 2 0 0 624 0 0.0 2015-09-13T03:00:00Z 756 3 0 0 null null 0.0 null 787 2 0 0 null null 0.0 null 860 58 0 0 199 0 0.0 2015-05-31T03:00:00Z 875 14 0 0 1638 0 0.0 2015-06-28T03:00:00Z 988 11 0 0 50 0 0.0 2015-09-13T03:00:00Z 1068 5 0 0 1135 0 0.0 2015-05-31T03:00:00Z 1077 2 0 0 1404 0 0.0 2015-09-13T03:00:00Z 1260 8 0 0 799 0 0.0 2015-06-28T03:00:00Z 1270 1 0 0 1605 0 0.0 2015-06-28T03:00:00Z 1342 4 1 0 126 1 0.0 2015-05-10T03:00:00Z 1352 1 0 0 1474 0 0.0 2015-05-24T03:00:00Z 1398 11 0 0 1203 0 0.0 2015-06-07T03:00:00Z 1415 25 0 0 911 0 0.0 2015-09-13T03:00:00Z 1417 1 0 0 null null 0.0 null 1496 5 0 0 1529 1 0.0 2015-08-16T03:00:00Z 1561 1 0 0 null null 0.0 null 1653 7 2 1 208 1 0.1429 2015-05-31T03:00:00Z 1689 12 0 0 1233 0 0.0 2015-06-07T03:00:00Z 1721 1 0 0 1680 1 0.0 2015-09-13T03:00:00Z 1777 1 0 0 769 0 0.0 2015-09-13T03:00:00Z 1826 2 0 0 1250 0 0.0 2015-06-07T03:00:00Z 1848 2 0 0 1483 0 0.0 2015-05-31T03:00:00Z 1892 13 0 0 528 1 0.0 2015-09-13T03:00:00Z 1896 13 0 0 1233 0 0.0 2015-05-10T03:00:00Z 1977 21 0 0 1248 0 0.0 2015-09-13T03:00:00Z 2003 1 0 0 null null 0.0 null 2006 28 2 0 558 1 0.0 2015-09-13T03:00:00Z 2044 2 0 0 null null 0.0 null 2090 5 0 0 null null 0.0 null 2113 4 0 0 1663 0 0.0 2015-09-13T03:00:00Z 2142 52 7 1 1135 1 0.0192 2015-05-17T03:00:00Z 2169 1 0 0 1390 0 0.0 2015-05-10T03:00:00Z 2288 32 0 0 333 0 0.0 2015-06-28T03:00:00Z 2294 7 0 0 1172 0 0.0 2015-05-24T03:00:00Z 2322 2 0 0 1317 0 0.0 2015-05-10T03:00:00Z 2355 1 0 0 769 0 0.0 2015-06-28T03:00:00Z 2396 12 0 0 274 1 0.0 2015-09-13T03:00:00Z 2502 1 0 0 133 0 0.0 2015-09-13T03:00:00Z 2521 41 0 0 1282 0 0.0 2015-09-13T03:00:00Z 2610 16 0 0 256 1 0.0 2015-09-13T03:00:00Z 2675 2 0 0 1301 0 0.0 2015-05-31T03:00:00Z 2684 1 0 0 null null 0.0 null 2711 100 7 1 411 1 0.01 2015-05-31T03:00:00Z 2738 1 0 0 449 1 0.0 2015-09-13T03:00:00Z 2748 13 0 0 491 0 0.0 2015-09-13T03:00:00Z 2752 1 0 0 null null 0.0 null 2833 4 0 0 1085 0 0.0 2015-09-13T03:00:00Z 2835 2 0 0 null null 0.0 null 2842 1 0 0 421 0 0.0 2015-06-28T03:00:00Z 2920 2 1 0 936 1 0.0 2015-05-10T03:00:00Z 2924 2 0 0 691 0 0.0 2015-05-31T03:00:00Z 2961 10 2 0 739 0 0.0 2015-09-13T03:00:00Z 2971 7 0 0 730 0 0.0 2015-09-13T03:00:00Z 3042 27 0 0 1051 0 0.0 2015-06-28T03:00:00Z 3069 7 0 0 null null 0.0 null 3149 1 0 0 1114 0 0.0 2015-09-13T03:00:00Z 3207 1 0 0 null null 0.0 null 3213 2 0 0 1172 0 0.0 2015-06-28T03:00:00Z 3216 2 0 0 984 0 0.0 2015-05-31T03:00:00Z 3228 1 0 0 683 0 0.0 2015-06-28T03:00:00Z 3264 7 0 0 996 0 0.0 2015-06-28T03:00:00Z 3306 2 0 0 64 0 0.0 2015-05-24T03:00:00Z 3328 2 0 0 null null 0.0 null 3359 1 0 0 984 0 0.0 2015-05-10T03:00:00Z 3441 4 0 0 828 0 0.0 2015-05-31T03:00:00Z 3450 13 0 0 1098 0 0.0 2015-06-28T03:00:00Z 3488 1 0 0 1210 0 0.0 2015-05-31T03:00:00Z 3595 2 0 0 1533 0 0.0 2015-09-13T03:00:00Z 3611 15 0 0 508 0 0.0 2015-05-10T03:00:00Z 3621 1 0 0 799 0 0.0 2015-06-28T03:00:00Z 3650 3 0 0 1172 0 0.0 2015-05-24T03:00:00Z 3725 12 0 0 243 0 0.0 2015-06-28T03:00:00Z 3727 9 1 0 1221 1 0.0 2015-05-10T03:00:00Z 3749 1 0 0 1578 0 0.0 2015-05-31T03:00:00Z 3792 2 0 0 619 0 0.0 2015-09-13T03:00:00Z 3814 4 0 0 618 1 0.0 2015-05-10T03:00:00Z 3834 1 0 0 173 0 0.0 2015-06-28T03:00:00Z 3886 2 0 0 828 0 0.0 2015-05-31T03:00:00Z 3905 2 0 0 598 0 0.0 2015-06-28T03:00:

Saving data to adls

In [0]:
dim_item.write.format("delta").mode("overwrite").option("overwriteSchema", "true").save("abfss://gold@project1azure1.dfs.core.windows.net/dim_item")
